[View in Colaboratory](https://colab.research.google.com/github/Santosh-Gupta/Book2Vec/blob/master/BookCrossingsAnalyzeEmbeddings.ipynb)

In [0]:
import re
from collections import Counter
import time

%matplotlib inline
from __future__ import print_function
import collections
import math
import numpy as np
import pandas as pd
import os
import random
import tensorflow as tf
from matplotlib import pyplot
from six.moves import range
from six.moves.urllib.request import urlretrieve
from sklearn.manifold import TSNE

from urllib.request import urlretrieve
from os.path import isfile, isdir
import zipfile
#import keras

!pip install -U -q PyDrive
!pip install adjustText #Helps prevent overlapping annotations on the scatter plots

from google.colab import files
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials
import sys
from adjustText import adjust_text
!pip install pillow 

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

Input Google Drive file for the Tensorflow Checkpoint

In [2]:
zip_id = input("Enter Gdrive file ID for tensorflow models: ") # you can use this file ID 1dPjSl7Q6ULsxVUMbRogfY1E-cA5cC1He

if not os.path.exists('MODEL'):
    os.makedirs('MODEL')

# DOWNLOAD ZIP
print ("Downloading zip file")
myzip = drive.CreateFile({'id': zip_id})
myzip.GetContentFile('model.zip')

# UNZIP ZIP
print ("Uncompressing zip file")
zip_ref = zipfile.ZipFile('model.zip', 'r')
zip_ref.extractall('MODEL/')
zip_ref.close()

print( os.getcwd() )
print( os.listdir('./MODEL') )

Enter Gdrive file ID for tensorflow models: 1dPjSl7Q6ULsxVUMbRogfY1E-cA5cC1He
Uncompressing zip file
/content
['checkpoint', 'bookVec.ckpt.meta', 'bookVec.ckpt.data-00000-of-00001', 'bookVec.ckpt.index']


Input Google drive file ID for the book info file produced in BookCrossingsDataAnalysis.ipynb notebook, create dictionaries for the book title and author

In [3]:
dl_id = input("Enter Gdrive file ID for books: ") # you can use this file ID 1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC

# DOWNLOAD ZIP
print ("Downloading  file")
myzip = drive.CreateFile({'id': dl_id})
myzip.GetContentFile('books.csv')

b = pd.read_csv( 'books.csv' )
b.head(30)
bookDictionary = b.set_index('EmbedID').to_dict()['Book_Title']
bookDictionary[5]
AuthorDictionary = b.set_index('EmbedID').to_dict()['Author']

Enter Gdrive file ID for books: 1thtwqN1fhyiLeEnmj51ZhEaW5DgonYgC


Extract the book embeddings for the input embedding matrix and softmax matrix.

In [4]:
with tf.Session() as sess:
  saver = tf.train.import_meta_graph('./MODEL/bookVec.ckpt.meta')
  saver.restore(sess, './MODEL/bookVec.ckpt' )

  embeddings = tf.get_default_graph().get_tensor_by_name('embeddings:0') #Getting regular embeddings
  softmax_weights = tf.get_default_graph().get_tensor_by_name('softmax_weights:0') #Get softmax embeddings
  
  normSM = tf.sqrt(tf.reduce_sum(tf.square(softmax_weights), 1, keepdims=True))
  normalized_embeddingsSM = softmax_weights / normSM
  
  norm = tf.sqrt(tf.reduce_sum(tf.square(embeddings), 1, keepdims=True))
  normalized_embeddings = embeddings / norm
  
  final_embeddings = normalized_embeddings.eval()
  final_embeddingsSM = normalized_embeddingsSM.eval()

INFO:tensorflow:Restoring parameters from ./MODEL/bookVec.ckpt


The following code blocks can look up the EmbedId from either the Author or Book Title. You don't have to use the exact author or title, you can just input a word and the code block will return all results which contain that word. 

In [18]:
#Use this code to get the book_id for any book using the authur name, using their full name, first name, or last name.  
#The search is case sensitive,  capitalize the first letter of any name. 

authorPhrase = 'Isaacson'
lines = []
for i in AuthorDictionary:
  if type(AuthorDictionary[i]) is str:
    if authorPhrase in AuthorDictionary[i] :
        lines.append(i)
for j in lines:
  print( bookDictionary[j], AuthorDictionary[j], ' | EmbedID: ', j  )

Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  34204
Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  37307


In [16]:
#Use this code to get the book_id for any book using the title, or a word in the title. 
#The search is case sensitive. All words in a title tend to be capitalized. 

searchPhrase = 'Wardrobe'
lines = []
for i in bookDictionary:
  if type(bookDictionary[i]) is str:
    if searchPhrase in bookDictionary[i] :
        lines.append(i)
for j in lines:
  print( bookDictionary[j], AuthorDictionary[j], ' | EmbedID: ', j  )

The Lion, the Witch and the Wardrobe (rpkg) (Narnia) C. S. Lewis  | EmbedID:  2426
Lion, the Witch and the Wardrobe C.S. Lewis  | EmbedID:  1051
The Lion, the Witch and the Wardrobe C. S. Lewis  | EmbedID:  25775
The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis  | EmbedID:  514
The Lion, the Witch and the Wardrobe (The Chronicles of Narnia) C. S. Lewis  | EmbedID:  7405
The Lion, the Witch and the Wardrobe (Full-Color Collector's Edition) C. S. Lewis  | EmbedID:  1895
Chic Simple Dress Smart for Women: Wardrobes that Win in the Workplace Kim Johnson Gross  | EmbedID:  29894
Brenda's Wardrobe Companion:  A Guide to Getting Dressed From the Inside Out Brenda Kinsel  | EmbedID:  30883
The Chronicles of Narnia: The Magician's Nephew/The Lion, the Witch and the Wardrobe/The Horse and His Boy/Prince Caspian/Voyage of the Dawn Treader/The Silver Chair/The Last Battle C. S. Lewis  | EmbedID:  22117
The Lion, the Witch, and the Wardrobe C.S. Lewis  | EmbedID:

The following code cells are show which books are most similiar to a particular book. The book_id is used to get its corresponding embedding, and then a dot product a calculated between that embedding and all other embeddings to find the most similiar embeddings. The most similiar embeddings have their corresponding book title and author names printed out, starting with the most similiar. 

In [8]:
#Harry Potter and the Prisoner of Azkaban (Book 3) J. K. Rowling  | EmbedID:  44

JaneA = np.take(final_embeddings, 44, axis=0)   
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

print('Most similiar to ', bookDictionary[nearestJaneA[0]], 'by',  AuthorDictionary[nearestJaneA[0]], '\n')

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Most similiar to  Harry Potter and the Prisoner of Azkaban (Book 3) by J. K. Rowling 

Harry Potter and the Prisoner of Azkaban (Book 3) J. K. Rowling
Harry Potter and the Chamber of Secrets (Book 2) J. K. Rowling
Harry Potter and the Goblet of Fire (Book 4) J. K. Rowling
Harry Potter and the Sorcerer's Stone (Book 1) J. K. Rowling
Harry Potter and the Order of the Phoenix (Book 5) J. K. Rowling
nan nan
1999 Writer's Market (Annual) Kirsten Holm
The Essential Calvin and Hobbes Bill Watterson
The Hanged Man T. J. MacGregor
Porno Irvine Welsh
The Lays of Beleriand (The History of Middle-Earth - Volume 3) J. R. R. Tolkien
nan nan
Caesar Colleen McCullough
So Long, and Thanks for All the Fish DOUGLAS ADAMS
The Book Lover's Kit Deborah Grandinetti


In [10]:
#James and the Giant Peach Roald Dahl  | EmbedID:  1492

JaneA = np.take(final_embeddings, 1492, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

James and the Giant Peach Roald Dahl
Good things: The best of Martha Stewart living Martha Stewart
The Secret of Platform 13 Eva Ibbotson
The Bridegroom: Stories (Vintage International (Paperback)) Ha Jin
Mara and Dann Doris Lessing
Sunset Limited James Lee Burke
Men, Women and Relationships John Gray
Dreams in the Golden Country: The Diary of Zipporah Feldman, a Jewish Immigrant Girl, New York City, 1903 (Dear America) Kathryn Lasky
River of Blue Fire (Otherland, Volume 2) Tad Williams
PRINCESS Jude Deveraux
The Pilot's Wife Anita Shreve
Christianity, Social Tolerance, and Homosexuality: Gay People in Western Europe from the Beginning of the Christian Era to the Fourteenth Century John Boswell
October Sky: A Memoir Homer Hickam
Shoulders: A Novel Georgia Cotrell
Reservation Road John Burnham Schwartz


In [14]:
#Pride and Prejudice Jane Austen  | EmbedID:  610

JaneA = np.take(final_embeddings, 610, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Pride and Prejudice Jane Austen
The Curious Sofa: A Pornographic Work by Ogdred Weary Edward Gorey
Emma JANE AUSTEN
So Long, and Thanks for All the Fish DOUGLAS ADAMS
Mystery Peter Straub
Final Fantasy VIII Official Strategy Guide David Cassady
A Tan and Sandy Silence (Travis McGee Mysteries) John D. MacDonald
The 776 Stupidest Things Ever Said Ross Petras
The Complete Idiot's Guide to Decoding Your Genes Linda Tagliaferro
Sense and Sensibility Jane Austen
The Empty House Rosamunde Pilcher
Mates, Dates, and Sole Survivors (Mates, Dates) Cathy Hopkins
Election: A Novel Tom Perrotta
Three Complete Novels: Daring to Dream/Holding the Dream/Finding the Dream (Dream) Nora Roberts
The House of Sleep (Vintage Contemporaries (Paperback)) Jonathan Coe


In [17]:
#The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis  | EmbedID:  514

JaneA = np.take(final_embeddings, 514, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

The Lion, the Witch, and the Wardrobe (The Chronicles of Narnia, Book 2) C. S. Lewis
The Horse and His Boy C. S. Lewis
The Magician's Nephew (rack) (Narnia) C. S. Lewis
The Last Battle C. S. Lewis
Prince Caspian (rack) : The Return to Narnia (Narnia) C. S. Lewis
Pug Shots Jim Dratfield
The Voyage of the Dawn Treader (rack) (Narnia) C. S. Lewis
Rachel's Tears: The Spiritual Journey of Columbine Martyr Rachel Scott Darrell Scott
The Broken Cord: A Family's Ongoing Struggle With Fetal Alcohol Syndrome Michael Dorris
Interview with the Vampire : Anniversary edition ANNE RICE
The Kill Fee (Van Womer, Laura) Laura Van Wormer
Trainspotting John Hodge
Night Shift Stephen King
nan nan
Haunted Schools: True Ghost Stories (True Ghost Stories) Allan Zullo


In [19]:
#Benjamin Franklin : An American Life Walter Isaacson  | EmbedID:  34204

JaneA = np.take(final_embeddings, 34204, axis=0) 
similarityJaneA = np.matmul(JaneA, np.transpose(final_embeddings))

nearestJaneA = (-similarityJaneA).argsort()[0:15]

for k in range(0, 15):
  print(bookDictionary[nearestJaneA[k]], AuthorDictionary[nearestJaneA[k]])

Benjamin Franklin : An American Life Walter Isaacson
Eating Well For Optimum Health: The Essential Guide to Bringing Health and Pleasure Back to Eating Andrew Weil
Perdido Street Station China Mieville
Amazing Gracie: A Dog's Tale Dan Dye
San Andreas Alistair MacLean
High Five (A Stephanie Plum Novel) Janet Evanovich
Ten Big Ones: A Stephanie Plum Novel Janet Evanovich
Barchester Towers (Penguin Classics) Anthony Trollope
Home Song Lavyrle Spencer
Night Of The Full Moon (Stepping Stone,  paper) GLORIA WHELAN
Thale's Folly Dorothy Gilman
nan nan
Last Orders Graham Swift
GHOST STY Peter Straub
Our Story: 77 Hours That Tested Our Friendship and Our Faith The Quecreek Miners


Of course, there are 40,886 other books to evaluate, but evaluating all those books would be very time-consuming. A way to evaluate a large number of books  is TSNE, which maps the embeddings into a 2D or 3D space where embeddings that are most similar to each other are plotted close to each other (more elegantly explained here https://www.youtube.com/watch?v=p3wFE85dAyY ). 

I performed a TSNE of the most occurring 2770 books for both the input embeddings and the softmax embeddings. For both sets of embeddings, the maps did not really make much sense to me. (you probably have to download these, open them up, and zoom in to read the maps)

In [0]:
num_points2 = 2770
books = [bookDictionary[i] for i in range(0, num_points2+1)]

tsne = TSNE(perplexity=50, n_components=2, init='pca', n_iter=5000, method='exact')
two_d_embeddings = tsne.fit_transform(final_embeddings[0:num_points2+1, :])

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
    
np.save('BookCrossings.npy', two_d_embeddings)  #TNSE may take a lot of time, so may be helpful to save the variable
uploadModel = drive.CreateFile()
uploadModel.SetContentFile('BookCrossings.npy')
uploadModel.Upload()

two_d_embeddingsSM = tsne.fit_transform(final_embeddingsSM[0:num_points2+1, :])

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
    
np.save('BookCrossingsSM.npy', two_d_embeddingsSM)  #TNSE may take a lot of time, so may be helpful to save the variable
uploadModel = drive.CreateFile()
uploadModel.SetContentFile('BookCrossingsSM.npy')
uploadModel.Upload()

Upload saved TSNE variable from Google drive using the Google Drive file ID of the numpy variable. 

In [7]:
loadModel = input("Would you like to load a TSNE varible? Type y or n ")  #  1ZgCG3KtUTVe8pUzlDiTHYOD5jXfbBAlQ

if loadModel == 'y':
  num_points2 = 3000
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  tsne_id = input("Enter Gdrive file ID for numpy variable: ") # 

  getTsne = drive.CreateFile({'id': tsne_id})
  getTsne.GetContentFile('tnsedl.npy')

  two_d_embeddingsLoaded2 = np.load('tnsedl.npy')

Would you like to load a TSNE varible? Type y or n y
Enter Gdrive file ID for numpy variable: 1rFFyYaut555jDb0Sr0QmefTdspWXzfp8


Plot the TSNE

In [10]:
auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)
uploadModel = drive.CreateFile()

# from adjustText import adjust_text
# import numpy as np
# import pandas as pd

texts = []

def plot(embeddings, labels):
  assert embeddings.shape[0] >= len(labels), 'More labels than embeddings'
  pyplot.figure(figsize=(130, 130))  # in inches best sofar 275
  print('step4')
  for i, label in enumerate(labels):
    x, y = embeddings[i,:]
    pyplot.scatter(x, y)
    #texts.append(pyplot.text(x[i], y[i], label))
    #pyplot.annotate(label, xy=(x, y), xytext=(5, 2), textcoords='offset points', 3
                   #ha='right', va='bottom')
    #pyplot.text(x, y, label) 
    texts.append(pyplot.text(x, y, label))
    
  print('step5')  
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  adjust_text(texts , arrowprops=dict(arrowstyle='->', color='#8f1402' , linewidth=0.7 ),  save_steps = False, save_prefix = 'Finalm', \
              autoalign = False ) #,  force_text=(0.2, 0.5 ), force_points=(0.4, 1.0), force_objects=(0.2, 0.5) got to 148 . try 110 next time
  
  print('step6')
  auth.authenticate_user()
  gauth = GoogleAuth()
  gauth.credentials = GoogleCredentials.get_application_default()
  drive = GoogleDrive(gauth)
  
  pyplot.savefig('Final2SM.jpg', bbox_inches='tight')
  uploadModel = drive.CreateFile()
  uploadModel.SetContentFile('Final2SM.jpg')
  uploadModel.Upload()
  
#   pyplot.savefig('Final2.png', bbox_inches='tight')
#   uploadModel = drive.CreateFile()
#   uploadModel.SetContentFile('Final2.png')
#   uploadModel.Upload()
  print('step7')
  #pyplot.show()


books = [bookDictionary[i] for i in range(1, num_points2+1)]
print('step3')
plot(two_d_embeddingsLoaded2, books)

step3
step4
step5
step6
step7
